In [ ]:
import pickle
import pandas as pd
import networkx as nx
import sys
import numpy as np
import torch
!pip install validators


In [ ]:
# Import the graph formed with NLP Feature vectors
with open('graph.pkl','rb') as f:
  g = pickle.load(f)

In [ ]:
df = pd.read_csv('labels.csv')

In [ ]:
nodes = list(df['link'])
labels = list(df['label'])

In [ ]:
A = nx.adjacency_matrix(g)
print('Graph info: ', nx.info(g))

Graph info:  Graph with 3984 nodes and 24895 edges


In [ ]:
# Label encoder for GNN
from sklearn.preprocessing import LabelEncoder
from tensorflow.keras.utils import to_categorical

def encode_label(labels):
    label_encoder = LabelEncoder()
    labels = label_encoder.fit_transform(labels)
    labels = to_categorical(labels)
    return labels, label_encoder.classes_

labels_encoded, classes = encode_label(labels)

In [ ]:
# Import packages
from urllib.request import urlopen
import requests
from bs4 import BeautifulSoup
import re
import nltk
import validators
nltk.download('words')
words = set(nltk.corpus.words.words())

def get_content(url):
    if (not validators.url(url)):
      return ""

    # Specify url of the web page
    source = requests.get(url).text

    # Make a soup 
    soup = BeautifulSoup(source,'lxml')

    # Extract the plain text content from paragraphs
    paras = []
    for paragraph in soup.find_all('p'):
        paras.append(str(paragraph.text))
    text = ''
    for i in paras:
        text += i.lower()

    text = re.sub(r"\[.*?\]+", ' ', text)
    text = re.sub(r"\{.*?\}+", ' ', text)
    text = re.sub(r"\(.*?\)+", ' ', text)
    text = re.sub(r"[0-9]+", ' ', text)
    text = re.sub(r"[Α-Ωα-ω]",' ',text)
    text = re.sub(r"\[A-Za-z0-9]+",' ',text)
    text = re.sub(r"[^\u0000-\u05C0\u2100-\u214F]+", ' ', text)
    text = re.sub(r"\\[a-zA-Z]+", ' ', text)
    text = re.sub("[^a-zA-Z'\n ]+", ' ', text)
    text = re.sub(r"\n", ' ', text)
    text = " ".join(w for w in nltk.wordpunct_tokenize(text) if w.lower() in words or not w.isalpha())

    return text

[nltk_data] Downloading package words to /root/nltk_data...
[nltk_data]   Unzipping corpora/words.zip.


In [ ]:
df.head()

title  label                                               link
0  Quadratic Equation     1   https://en.wikipedia.org/wiki/Quadratic_equation
1    Complex Numbers      1       https://en.wikipedia.org/wiki/Complex_number
2       Bayes Theorem     2     https://en.wikipedia.org/wiki/Bayes%27_theorem
3      Straight Lines     1      https://en.wikipedia.org/wiki/Line_(geometry)
4           Functions     1  https://en.wikipedia.org/wiki/Function_(mathem...

In [ ]:
(df.loc[df['link'] == 'https://en.wikipedia.org/wiki/Quadratic_equation', 'label'])

0      1
203    1
378    1
464    1
754    1
800    1
813    1
Name: label, dtype: object

In [ ]:
# Forming a dictionary of training set with labels and content

data_dict = {}
for link in df['link']:
  lst = list(df.loc[df['link'] == link, 'label'])
  lst = [i for i in lst if i in ['0','1','2','3']]
  if (lst == []):
    continue
  res = max(set(lst), key = lst.count)
  data_dict[link] = [res,'url']




In [ ]:
# Adding content for the given urls in the training data
i = 0
for link in data_dict.keys():
  x = get_content(link)
  if (x == ""):
    continue
  data_dict[link][1] = x
  i += 1
    
  
  sys.stdout.write(f"\rNumber of Articles completed: {i}")
  sys.stdout.flush()


Number of Articles completed: 531

In [ ]:
g.nodes()
# for key in data_dict:
# topics_dataset2['Link'][0]

NodeView((0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153, 154, 155, 156, 157, 158, 159, 160, 161, 162, 163, 164, 165, 166, 167, 168, 169, 170, 171, 172, 173, 174, 175, 176, 177, 178, 179, 180, 181, 182, 183, 184, 185, 186, 187, 188, 189, 190, 191, 192, 193, 194, 195, 196, 197, 198, 199, 200, 201, 202, 203, 204, 205, 206, 207, 208, 209, 210, 211, 212, 213, 214, 215, 216, 217, 218, 219, 

In [ ]:
j = 0
for i in g.nodes():
  if (topics_dataset2['Link'][i] in list(data_dict.keys())):
    j += 1
print(j)
# fg = [i[1] for i in list(data_dict.values())]
# print(list(topics_dataset2.keys()))

In [1]:
# Open dataframe
import pickle
with open('dataframe.pkl','rb') as f:
  topics_dataset2 = pickle.load(f)

In [ ]:
k = 0
for i in data_dict.keys():
  if (i in list(topics_dataset2['Link'])):
    k += 1

print(k)


225


In [ ]:
labels = []
nodes = []
X = []
for i in data_dict:
  labels.append(data_dict[i][0])
  nodes.append(i)
  X.append(data_dict[i][1])


In [ ]:
import numpy as np
import pandas as pd
import re
from nltk.corpus import stopwords
from nltk.stem.porter import PorterStemmer
from sklearn.feature_extraction.text import TfidfVectorizer
port_stem = PorterStemmer()

def stemming(Content):
    # stemmed_content = re.sub('[^a-zA-Z]',' ',Content)
    # stemmed_content = stemmed_content.lower()
    stemmed_content = Content.split()
    stemmed_content = [port_stem.stem(word) for word in stemmed_content 
                       if not word in stopwords.words('english')]
    stemmed_content = ' '.join(stemmed_content)
    return stemmed_content

In [ ]:
for i in range(len(X)):
  X[i] = stemming(X[i])


In [ ]:
from sklearn.feature_extraction.text import TfidfVectorizer

# instantiate the vectorizer object
# use analyzer is word and stop_words is english which are responsible for remove stop words and create word vocabulary
tfidfvectorizer = TfidfVectorizer(analyzer='word' , stop_words='english',)
tfidfvectorizer.fit(X)
tfidf_term_vectors  = tfidfvectorizer.transform(X)
print("Sparse Matrix form of test data : \n")
H = tfidf_term_vectors.todense()
print(H)

Sparse Matrix form of test data : 

[[0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]]


In [ ]:
print(H.shape)

(545, 6170)


In [ ]:

from sklearn.decomposition import TruncatedSVD
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import Normalizer


import sys
from time import time

import numpy as np

In [ ]:
true_k= 1000

r = true_k
t0 = time()
svd = TruncatedSVD(r)
normalizer = Normalizer(copy=False)
lsa = make_pipeline(svd, normalizer)
SVD_Y = lsa.fit_transform(H)
print("done in %fs" % (time() - t0))

/home/chaitanya/.local/lib/python3.9/site-packages/sklearn/utils/validation.py:593: FutureWarning: np.matrix usage is deprecated in 1.0 and will raise a TypeError in 1.2. Please convert to a numpy array with np.asarray. For more information see: https://numpy.org/doc/stable/reference/generated/numpy.matrix.html
  warnings.warn(


done in 8.777078s


In [ ]:
X1 = []
for i in range(len(X)):
  X1.append(SVD_Y[i])

In [ ]:
X1

[array([ 3.00023907e-01, -9.54081405e-02, -9.05180932e-02, -1.06923662e-15,
         8.13636128e-02, -3.58304572e-03,  3.82586931e-02,  4.03517599e-01,
        -8.77543877e-02, -2.00711704e-01, -1.10001697e-01,  1.25759037e-02,
        -2.70547146e-01, -1.01995661e-01, -2.46131119e-01,  1.63410856e-02,
        -2.28226659e-01,  3.62258989e-02,  2.59556406e-01,  4.60730535e-02,
        -1.94175134e-01,  6.77878347e-02, -1.28233650e-01, -1.99264630e-02,
         1.00865750e-01, -4.04946854e-01,  2.98793310e-02, -6.04055627e-02,
        -1.06143746e-01,  5.13475343e-02, -1.72200666e-02,  2.74805384e-02,
         2.68766783e-02, -3.75631524e-02,  3.23260896e-02, -1.09652461e-01,
         5.52973476e-02,  2.97769133e-02, -4.60699043e-02,  9.40446157e-03,
         5.01684423e-02,  7.66347859e-02, -1.13465126e-01, -4.09872749e-02,
        -1.27305590e-01, -1.84473721e-02,  2.88277243e-02,  9.05071011e-02,
         2.87314861e-02,  5.18982978e-02,  3.18991038e-04,  3.10008889e-02,
        -2.1

In [ ]:
X = np.array(X1,dtype=int)


In [ ]:
N = X.shape[0] #the number of nodes


In [ ]:
F = X.shape[1] #the size of node features


In [ ]:
def limit_data(labels,limit=20,val_num=200,test_num=245):
    '''
    Get the index of train, validation, and test data
    '''
    label_counter = dict((l, 0) for l in labels)
    train_idx = []

    for i in range(len(labels)):
        label = labels[i]
        if label_counter[label]<limit:
            #add the example to the training data
            train_idx.append(i)
            label_counter[label]+=1
        
        #exit the loop once we found 20 examples for each class
        if all(count == limit for count in label_counter.values()):
            break
    
    #get the indices that do not go to traning data
    rest_idx = [x for x in range(len(labels)) if x not in train_idx]
    val_idx = rest_idx[:val_num]
    test_idx = rest_idx[val_num:(val_num+test_num)]
    return train_idx, val_idx,test_idx

train_idx,val_idx,test_idx = limit_data(labels)

#set the mask
train_mask = np.zeros((N,),dtype=bool)
train_mask[train_idx] = True

val_mask = np.zeros((N,),dtype=bool)
val_mask[val_idx] = True

test_mask = np.zeros((N,),dtype=bool)
test_mask[test_idx] = True

In [ ]:
#obtain the adjacency matrix (A)
A = nx.adjacency_matrix(g)
print('Graph info: ', nx.info(g))

Graph info:  Name: 
Type: Graph
Number of nodes: 3984
Number of edges: 24895
Average degree:  12.4975


In [ ]:
def encode_label(labels):
    label_encoder = LabelEncoder()
    labels = label_encoder.fit_transform(labels)
    labels = to_categorical(labels)
    return labels, label_encoder.classes_

labels_encoded, classes = encode_label(labels)

In [ ]:
from dgl.nn.pytorch import GraphConv

# Parameters
channels = 16           # Number of channels in the first layer
dropout = 0.5           # Dropout rate for the features
l2_reg = 5e-4           # L2 regularization rate
learning_rate = 1e-2    # Learning rate
epochs = 200            # Number of training epochs
es_patience = 10        # Patience for early stopping

# Preprocessing operations
A = GraphConv.preprocess(A).astype('f4')

# Model definition
X_in = Input(shape=(F, ))
fltr_in = Input((N, ), sparse=True)

dropout_1 = Dropout(dropout)(X_in)
graph_conv_1 = GraphConv(channels,
                         activation='relu',
                         kernel_regularizer=l2(l2_reg),
                         use_bias=False)([dropout_1, fltr_in])

dropout_2 = Dropout(dropout)(graph_conv_1)
graph_conv_2 = GraphConv(num_classes,
                         activation='softmax',
                         use_bias=False)([dropout_2, fltr_in])

# Build model
model = Model(inputs=[X_in, fltr_in], outputs=graph_conv_2)
optimizer = Adam(lr=learning_rate)
model.compile(optimizer=optimizer,
              loss='categorical_crossentropy',
              weighted_metrics=['acc'])
model.summary()

tbCallBack_GCN = tf.keras.callbacks.TensorBoard(
    log_dir='./Tensorboard_GCN_cora',
)
callback_GCN = [tbCallBack_GCN]